# Install all necessary packages, hopefully should work without needing to go into pawsey directories with singularity shell

# MOVE The transformers folder from /src/ in the DNABERT repo to where packages are stored /home/mgill/.local/lib/python3.8/site-package

In [ ]:
#Bug where it installs wrong transformers for some reason in wrong spot, this should fix it

!python3 -m pip install --editable .
!python3 -m pip install torch==1.4 torchvision
!python3 -m pip install tensorflow tensorboardX tensorboard seqeval pyahocorasick scipy statsmodels biopython pandas pybedtools sentencepiece==0.1.91 scikit-learn>=0.22.2
!python3 -m pip install ipywidgets

####MOVE The transformers folder from /src/ in the DNABERT repo to where packages are stored /home/mgill/.local/lib/python3.8/site-package

In [ ]:
!TMPDIR=/home/mgill/ python3 -m pip install scikit-cuda fastai==1.0.61 biopython

In [ ]:
!TMPDIR=/home/mgill/ python3 -m pip install networkx

In [ ]:
!pip list

In [ ]:
from fastai import *
from fastai.text import *
from Bio import Seq
from Bio.Seq import Seq
from Bio import SeqIO
from Bio.SeqRecord import SeqRecord
from Bio.SeqFeature import FeatureLocation, CompoundLocation
import networkx as nx
import pandas as pd

# Before continuing on ensure you have run script to retrieve fasta from GFF3s (from cantata and ensembl) and random streteches of DNA

### Run Script Below. Needs to have a ref genome file ending in {whatever}_ref.fa
### Needs to have genome info file ending in {whatever}_genome_file.genome
### both need to be in same folder as script

# run bash script below on server with pandas and numpy
# arg1 being url for lncrna, arg2 url for mrna, change URL for each crop

bash create_fasta_from_url.sh http://cantata.amu.edu.pl/DOWNLOADS/Arabidopsis_thaliana_lncrnas.gtf ftp://ftp.ensemblgenomes.org/pub/plants/release-51/gff3/arabidopsis_thaliana/Arabidopsis_thaliana.TAIR10.51.gff3.gz

# Preprocess Data From Fasta of lncrna, mrna and random to TSV's
### Based upon g-ulmfit conversion of fasta to csv
### then DNABERT (with some of my edits) from csv format to kmer tab delimited TSV's

In [ ]:
#set filenames to string
#mrna = 'mrna_ensembl.gff3unique.gff3_flanked.fa'
#lncrna1 = 'lncRNAs_with_gene_cantata.gff3unique.gff3_flanked.fa'
lncrna = 'bo_lncrna_flanked.fa'
#randrna1 = 'random_intervals_flanked_w.fa'
randrna = 'random_fasta_flanked.fa'

In [ ]:
#read fasta file
#creates DF with column of fasta string and a 2nd column of whether it was mRNA, lncRNA etc.
def parse_fasta(filename, label):
    fasta = SeqIO.parse(filename, 'fasta')
    fs = [i for i in fasta]
    seqs = [str(i.seq) for i in fs]
    df = pd.DataFrame(seqs, columns=['Sequence'])
    df['Target'] = label
    df = df.drop_duplicates()
    return df

In [ ]:
#create df for each set of transcripts
#mrna_df = parse_fasta(mrna, "not_lncRNA")
#lncrna_df1 = parse_fasta(lncrna1, "lncRNA")
lncrna_df = parse_fasta(lncrna, "lncRNA")
#random_df1 = parse_fasta(randrna1, "not_lncRNA")
random_df = parse_fasta(randrna, "not_lncRNA")

In [ ]:
#mrna_df=mrna_df.sample(1000)
#mrna_df.shape
#print(mrna_df)

In [ ]:
#random_df=random_df.sample(4000)
#random_df.shape
#print(random_df)

In [ ]:
total = 0
for x in range(0,random_df2.shape[0]):
    y=len(random_df2.iloc[x]["Sequence"])
    total=total+y
print(total)
    
print(str(total/random_df2.shape[0]))

total = 0
for x in range(0,lncrna_df2.shape[0]):
    y=len(lncrna_df2.iloc[x]["Sequence"])
    if(y>total):
        total=y
print(total)
    
print(str(total/lncrna_df2.shape[0]))

In [ ]:
#divide data into a holdout set and training test set, hardcoded at 80/20 split
def partition_data(df):
    
    train_size = int(len(df)*0.80)
    ho_size = int(len(df)) - train_size
    
    train_df = df.sample(train_size)
    ho_df = df.drop(train_df.index)
    #final column of what it was set to 
    train_df['set'] = 'train'
    ho_df['set'] = 'holdout'
    
    return train_df, ho_df

In [ ]:
#split data into training and holdout
#train_mrna_df, ho_mrna_df = partition_data(mrna_df)
#train_lncrna_df, ho_lncrna_df = partition_data(lncrna_df1)
train_lncrna_df, ho_lncrna_df = partition_data(lncrna_df)
#train_random_df1, ho_random_df1 = partition_data(random_df1)
train_random_df, ho_random_df = partition_data(random_df)

In [ ]:
#concat all training data together and holdout data together
train_test_df = pd.concat([train_lncrna_df, train_random_df], axis = 0, ignore_index = True)
holdout_df = pd.concat([ho_lncrna_df, ho_random_df], axis = 0, ignore_index = True)

In [ ]:
#drop set column
train_test_df.drop("set", axis = 1, inplace = True)
holdout_df.drop("set", axis = 1, inplace = True)

forbidden_strings = ['N', 'Y', 'D', 'S', 'K', 'W', 'M', 'R', 'V', 'H', 'B']

#check shape before removal
print(train_test_df.shape)
print(holdout_df.shape)

#Remove any rows with forbidden strings in sequence by equalling rows that don't (~) have 'forbidden string' in sequence
for S in forbidden_strings:
    train_test_df = train_test_df[~train_test_df.Sequence.map(lambda x: S in x.upper())]
    holdout_df = holdout_df[~holdout_df.Sequence.map(lambda x: S in x.upper())]

#check shape after removal
print(train_test_df.shape)
print(holdout_df.shape)

In [ ]:
#shuffle
train_test_df = train_test_df.sample(frac=1)
print(train_test_df)
holdout_df = holdout_df.sample(frac=1)
print(holdout_df)

#save to file
train_test_df.to_csv("train_test.csv", index=False)
holdout_df.to_csv("holdout.csv", index=False)

In [ ]:
#Unccoment first time you run this cell
#!mv motif/motif_utils.py .
from motif_utils import *
import sys
def csv_to_dnabert_tsv(in_string, out_string, kmer):
    csv_file = in_string
    my_k = kmer
    df = pd.read_csv(csv_file)
    seq_array = []
    label_array = []
    for i, row in df.iterrows():
        seq = row["Sequence"]
        label = row["Target"]
        seq = seq2kmer(seq,my_k)
        seq_array.append(seq)
        if(label == "lncRNA"):
               label = 0
        else:
               label = 1
        label_array.append(label)
        print(label)
    data = np.array([seq_array, label_array])
    data = data.T
    print(data)
    new_df = pd.DataFrame(data, columns=["sequence", "label"], index=None)
    print(new_df)
    new_df.to_csv(out_string, sep="\t", header=True, index=False)

In [ ]:
#Should now be in format that is DNABERT friendly, output has to be train.tsv and dev.tsv for DNABERT
#final arg is kmer size, adjust for which model you've downloaded from their pretrained
csv_to_dnabert_tsv("train_test.csv", "train.tsv", 3)
csv_to_dnabert_tsv("holdout.csv", "dev.tsv", 3)
!mv *.tsv input_data_3mer/

csv_to_dnabert_tsv("train_test.csv", "train.tsv", 4)
csv_to_dnabert_tsv("holdout.csv", "dev.tsv", 4)
!mv *.tsv input_data_4mer/

csv_to_dnabert_tsv("train_test.csv", "train.tsv", 5)
csv_to_dnabert_tsv("holdout.csv", "dev.tsv", 5)
!mv *.tsv input_data_5mer/

csv_to_dnabert_tsv("train_test.csv", "train.tsv", 6)
csv_to_dnabert_tsv("holdout.csv", "dev.tsv", 6)
!mv *.tsv input_data_6mer/

# Fine Tune Models with Arabidopsis Data

## 3mer

In [ ]:
#torch.cuda.empty_cache()
#hardocded the variables, not sure how to do this with env variables above :(
#!mv examples/run_finetune.py .
%run run_finetune.py \
    --model_type dnalongcat \
    --tokenizer_name=dna3 \
    --model_name_or_path=/group/pawsey0149/mgill/dl_playground/DNABERT_Bo/3-new-12w-0/ \
    --task_name dnaprom \
    --do_train \
    --do_eval \
    --data_dir /group/pawsey0149/mgill/dl_playground/DNABERT_Bo/input_data_3mer \
    --max_seq_length 2048 \
    --per_gpu_eval_batch_size=4   \
    --per_gpu_train_batch_size=4   \
    --learning_rate 2e-5 \
    --num_train_epochs 4.0 \
    --output_dir /group/pawsey0149/mgill/dl_playground/DNABERT_Bo/output_data_3mer/ \
    --evaluate_during_training \
    --logging_steps 100 \
    --save_steps 4000 \
    --warmup_percent 0.1 \
    --hidden_dropout_prob 0.1 \
    --overwrite_output \
    --weight_decay 0.01 \
    --n_process 8

In [ ]:
%run run_finetune.py \
    --model_type dnalongcat \
    --tokenizer_name=dna3 \
    --model_name_or_path /group/pawsey0149/mgill/dl_playground/DNABERT_Bo/output_data_3mer/ \
    --task_name dnaprom \
    --do_predict \
    --data_dir /group/pawsey0149/mgill/dl_playground/DNABERT_Bo/input_data_3mer \
    --max_seq_length 2048 \
    --per_gpu_pred_batch_size=8   \
    --output_dir /group/pawsey0149/mgill/dl_playground/DNABERT_Bo/output_data_3mer/ \
    --predict_dir /group/pawsey0149/mgill/dl_playground/DNABERT_Bo/results_3mer/

## 4mer

In [ ]:
#hardocded the variables, not sure how to do this with env variables above :(
#!mv examples/run_finetune.py .
%run run_finetune.py \
    --model_type dnalongcat \
    --tokenizer_name=dna4 \
    --model_name_or_path=/group/pawsey0149/mgill/dl_playground/DNABERT_Bo/4-new-12w-0/ \
    --task_name dnaprom \
    --do_train \
    --do_eval \
    --data_dir /group/pawsey0149/mgill/dl_playground/DNABERT_Bo/input_data_4mer/ \
    --max_seq_length 2048 \
    --per_gpu_eval_batch_size=2   \
    --per_gpu_train_batch_size=2   \
    --learning_rate 2e-5 \
    --num_train_epochs 4.0 \
    --output_dir /group/pawsey0149/mgill/dl_playground/DNABERT_Bo/output_data_4mer/ \
    --evaluate_during_training \
    --logging_steps 100 \
    --save_steps 4000 \
    --warmup_percent 0.1 \
    --hidden_dropout_prob 0.1 \
    --overwrite_output \
    --weight_decay 0.01 \
    --n_process 8

In [ ]:
%run run_finetune.py \
    --model_type dnalongcat \
    --tokenizer_name=dna4 \
    --model_name_or_path /group/pawsey0149/mgill/dl_playground/DNABERT_Bo/output_data_4mer/ \
    --task_name dnaprom \
    --do_predict \
    --data_dir /group/pawsey0149/mgill/dl_playground/DNABERT_Bo/input_data_4mer \
    --max_seq_length 2048 \
    --per_gpu_pred_batch_size=8   \
    --output_dir /group/pawsey0149/mgill/dl_playground/DNABERT_Bo/output_data_4mer/ \
    --predict_dir /group/pawsey0149/mgill/dl_playground/DNABERT_Bo/results_4mer/

## 5mer

In [ ]:
#hardocded the variables, not sure how to do this with env variables above :(
#!mv examples/run_finetune.py .
%run run_finetune.py \
    --model_type dnalongcat \
    --tokenizer_name=dna5 \
    --model_name_or_path=/group/pawsey0149/mgill/dl_playground/DNABERT_Bo/5-new-12w-0/ \
    --task_name dnaprom \
    --do_train \
    --do_eval \
    --data_dir /group/pawsey0149/mgill/dl_playground/DNABERT_Bo/input_data_5mer/ \
    --max_seq_length 2048 \
    --per_gpu_eval_batch_size=4   \
    --per_gpu_train_batch_size=4   \
    --learning_rate 2e-5 \
    --num_train_epochs 4.0 \
    --output_dir /group/pawsey0149/mgill/dl_playground/DNABERT_Bo/output_data_5mer/ \
    --evaluate_during_training \
    --logging_steps 100 \
    --save_steps 4000 \
    --warmup_percent 0.1 \
    --hidden_dropout_prob 0.1 \
    --overwrite_output \
    --weight_decay 0.01 \
    --n_process 8

In [ ]:
%run run_finetune.py \
    --model_type dnalongcat \
    --tokenizer_name=dna5 \
    --model_name_or_path /group/pawsey0149/mgill/dl_playground/DNABERT_Bo/output_data_5mer/ \
    --task_name dnaprom \
    --do_predict \
    --data_dir /group/pawsey0149/mgill/dl_playground/DNABERT_Bo/input_data_5mer \
    --max_seq_length 2048 \
    --per_gpu_pred_batch_size=8   \
    --output_dir /group/pawsey0149/mgill/dl_playground/DNABERT_Bo/output_data_5mer/ \
    --predict_dir /group/pawsey0149/mgill/dl_playground/DNABERT_Bo/results_5mer/

## 6mer

In [ ]:
#hardocded the variables, not sure how to do this with env variables above :(
#!mv examples/run_finetune.py .
%run run_finetune.py \
    --model_type dnalongcat \
    --tokenizer_name=dna6 \
    --model_name_or_path=/group/pawsey0149/mgill/dl_playground/DNABERT_Bo/6-new-12w-0/ \
    --task_name dnaprom \
    --do_train \
    --do_eval \
    --data_dir /group/pawsey0149/mgill/dl_playground/DNABERT_Bo/input_data_6mer/ \
    --max_seq_length 2048 \
    --per_gpu_eval_batch_size=4   \
    --per_gpu_train_batch_size=4   \
    --learning_rate 2e-5 \
    --num_train_epochs 4.0 \
    --output_dir /group/pawsey0149/mgill/dl_playground/DNABERT_Bo/output_data_6mer/ \
    --evaluate_during_training \
    --logging_steps 100 \
    --save_steps 4000 \
    --warmup_percent 0.1 \
    --hidden_dropout_prob 0.1 \
    --overwrite_output \
    --weight_decay 0.01 \
    --n_process 8

In [ ]:
%run run_finetune.py \
    --model_type dnalongcat \
    --tokenizer_name=dna6 \
    --model_name_or_path /group/pawsey0149/mgill/dl_playground/DNABERT_Bo/output_data_6mer/ \
    --task_name dnaprom \
    --do_predict \
    --data_dir /group/pawsey0149/mgill/dl_playground/DNABERT_Bo/input_data_6mer \
    --max_seq_length 2048 \
    --per_gpu_pred_batch_size=8   \
    --output_dir /group/pawsey0149/mgill/dl_playground/DNABERT_Bo/output_data_6mer/ \
    --predict_dir /group/pawsey0149/mgill/dl_playground/DNABERT_Bo/results_6mer/

# DNABERT Motif Analysis

In [ ]:
#Run the attention score generation
%run run_finetune.py \
    --model_type dnalongcat \
    --tokenizer_name=dna3 \
    --model_name_or_path /group/pawsey0149/mgill/dl_playground/DNABERT_Bo/output_data_3mer/ \
    --task_name dnaprom \
    --do_visualize \
    --visualize_data_dir /group/pawsey0149/mgill/dl_playground/DNABERT_Bo/input_data_3mer/ \
    --data_dir /group/pawsey0149/mgill/dl_playground/DNABERT_Bo/input_data_3mer/ \
    --max_seq_length 2048 \
    --per_gpu_pred_batch_size=8   \
    --output_dir /group/pawsey0149/mgill/dl_playground/DNABERT_Bo/output_data_3mer/ \
    --predict_dir /group/pawsey0149/mgill/dl_playground/DNABERT_Bo/results_3mer/

In [ ]:
#test attention scores have been loaded
import numpy as np
my_at = np.load("/group/pawsey0149/mgill/dl_playground/DNABERT_Bo/results_3mer/atten.npy")
print(my_at.shape)

In [ ]:
#To make a reduced dataset
import pandas as pd

big_dev = pd.read_csv("holdout.csv")
print(big_dev)
labels = big_dev['Target']
pos = 0
neg = 0
for x in labels:
    if x=='lncRNA':
        pos = pos + 1
    else:
        neg = neg + 1
        
print(pos)
print(neg)

In [ ]:
#Visualise
# N = total seqs
# K = total positive seqs
# n = total motifs found in N seqs
# x = total motifs found in pos seqs
%run find_motifs.py \
    --data_dir /group/pawsey0149/mgill/dl_playground/DNABERT_Bo/input_data_3mer \
    --predict_dir /group/pawsey0149/mgill/dl_playground/DNABERT_Bo/results_3mer/ \
    --window_size 24 \
    --min_len 5 \
    --pval_cutoff 0.05 \
    --min_n_motif 3 \
    --align_all_ties \
    --save_file_dir /group/pawsey0149/mgill/dl_playground/DNABERT_Bo/results_3mer/ \
    --verbose

# Transformers Interpret Word Cloud

In [ ]:
import random as rand
import numpy as np
my_rand = [0] * 2500
#my_rand = np.zeros(520)
i = 0
while i < len(my_rand):
    x = rand.randint(4,9)
    my_rand[i] = x
    i = i + 1
test = [0] * 2048
#test = np.zeros(2048)

j = 0
flag = True
while j < 4 and flag == True:
    z = j*512
    print(z)
    test[z] = 2
    if(z+510 > len(my_rand)):
        leftover = len(my_rand) - j*510 + 1
        test[z+1:z+leftover] = my_rand[j*510:len(my_rand)]
    else:
        test[z+1:z+511] = my_rand[j*510:j*510+510]
    if(len(my_rand) < j*510+510):
        flag = False
    else:
        test[z+511] = 3
    j = j + 1

print(len(test))
print(test)

In [ ]:
for x in range(0,4):
    print(x)

In [1]:
import torch
from transformers import AutoTokenizer, AutoModel, AutoConfig
from transformers import BertForLongSequenceClassification, BertForSequenceClassification
from transformers_interpret import SequenceClassificationExplainer

#load variables for the classification explainer
config = AutoConfig.from_pretrained("output_data_3mer/", output_attentions=True)
tokenizer = AutoTokenizer.from_pretrained("output_data_3mer/")
#have to use custom LONG bert model
model = BertForLongSequenceClassification.from_pretrained("output_data_3mer/", config=config)

#load classification explainer
cls_explainer = SequenceClassificationExplainer(
    model,
    tokenizer)



<class 'transformers.tokenization_bert.BertTokenizerFast'>


In [2]:
import pandas as pd
import numpy as np

#load the holdout data
holdout = pd.read_csv("input_data_3mer/dev.tsv", sep = "\t")

#finds the indexes that were predicted to be 0 (aka lncRNA)
#and matches it with the labels that were ACTUALLY 0
#returns indexes of these matches to minimise cls explainers to go through
pred_results = np.load("results_3mer/pred_results.npy")
my_df = pd.read_csv("input_data_3mer/dev.tsv", sep = "\t")
#print(my_df)
targets = np.array(my_df["label"])
rounded_preds = [int(round(value)) for value in pred_results]
lncrna_idx = []
count = 0
print(len(targets))
print(len(rounded_preds))
while count < len(targets):
    #if target matches prediction and the prediction is for a lncrna store count in lncrna_idx
    if((targets[count] == 0)):
      #  print(count)
        lncrna_idx.append(count)
    count = count + 1
print((len(lncrna_idx)))

1618
1618
851


In [3]:
#inputs a set of word attributions from cls explainer and the current motif dictionary
#returns and updated motif dictionary
#mc in a dictionary with the motif and the number of times it appears
def make_motif_dict(word_attributions, motif_coll, mc):
    motif = ''
    motif_val = 0
    for x in range(len(word_attributions)):
        y = word_attributions[x]
        current_string = y[0]
        if(current_string != '[PAD]' and current_string != '[CLS]' and current_string != '[SEP]'):
            value = y[1]
            if(value>0):
                if(motif==''):
                    motif=current_string
                    motif_val = value
                else:
                    #change this value to be the length of kmer - 1 so that way we just adding the new base
                    motif=motif+current_string[2]
                    motif_val = motif_val + value
            else:
                if(len(motif)<7): ##makes sure its more than just a codon
                    motif = ''
                if(motif != ''):
                    #print('finished motif')
                    #print(motif)
                    #print(motif_val)
                    if motif in motif_coll:
                        print('we found a double boys yeehaw')
                        old_val = motif_coll.get(motif)
                        new_val = motif_val + old_val
                       # print(old_val)
                       # print(new_val)
                        #gets current count for motif, adds 1 and updates the motif_count dict
                        mc_old = mc.get(motif)
                        mc_new = mc_old + 1
                        motif_coll.update({motif:new_val})
                        print("motif: "+str(motif) + "   count: " + str(mc_new))
                        mc.update({motif:mc_new})
                    else:
                        mc[motif] = 1
                        motif_coll[motif] = motif_val
                        motif = ''
    return motif_coll, mc

In [4]:
#goes through each sequence that is lncRNA and is predicted be lncRNA from model

#goes through each sequence that is lncRNA and is predicted be lncRNA from model

m = {}
m_count = {}
for i in (lncrna_idx):
   # if(i>100):
   #     break
    example = holdout['sequence'][i]
    print(i)
    word_attributions = cls_explainer(example)
    print("predicted index from cls: " + str(cls_explainer.predicted_class_index))
    if(cls_explainer.predicted_class_index == 0):
        m,m_count = make_motif_dict(word_attributions, m, m_count)


1
this is embeddings: Embedding(69, 768, padding_idx=0)
this is the indexes: None
this is the class name: None
3
2048
ref id length is: 2048
this is self input ids before preds call: tensor([[ 2, 30, 42,  ...,  0,  0,  0]])
this is input ids before ligattributionstensor([[ 2, 30, 42,  ...,  0,  0,  0]])
this is input ids shape before preds call: torch.Size([1, 2048])
this is position shape: torch.Size([1, 2048])
new pos ids = tensor([[  0,   1,   2,  ..., 509, 510, 511],
        [  0,   1,   2,  ..., 509, 510, 511],
        [  0,   1,   2,  ..., 509, 510, 511],
        [  0,   1,   2,  ..., 509, 510, 511]])
this is AM: tensor([1., 1., 1.,  ..., 0., 0., 0.])
this is input ids shape before preds call: torch.Size([1, 2048])
this is position shape: torch.Size([1, 2048])
new pos ids = tensor([[  0,   1,   2,  ..., 509, 510, 511],
        [  0,   1,   2,  ..., 509, 510, 511],
        [  0,   1,   2,  ..., 509, 510, 511],
        [  0,   1,   2,  ..., 509, 510, 511]])
this is AM: tensor([1., 

predicted index from cls: 0
this is self input ids before preds call: tensor([[ 2, 21,  5,  ..., 60, 35,  3]])
11
this is embeddings: Embedding(69, 768, padding_idx=0)
this is the indexes: None
this is the class name: None
2
2048
ref id length is: 2048
this is self input ids before preds call: tensor([[ 2, 28, 35,  ...,  0,  0,  0]])
this is input ids before ligattributionstensor([[ 2, 28, 35,  ...,  0,  0,  0]])
this is input ids shape before preds call: torch.Size([1, 2048])
this is position shape: torch.Size([1, 2048])
new pos ids = tensor([[  0,   1,   2,  ..., 509, 510, 511],
        [  0,   1,   2,  ..., 509, 510, 511],
        [  0,   1,   2,  ..., 509, 510, 511],
        [  0,   1,   2,  ..., 509, 510, 511]])
this is AM: tensor([1., 1., 1.,  ..., 0., 0., 0.])
this is input ids shape before preds call: torch.Size([1, 2048])
this is position shape: torch.Size([1, 2048])
new pos ids = tensor([[  0,   1,   2,  ..., 509, 510, 511],
        [  0,   1,   2,  ..., 509, 510, 511],
     

this is self input ids before preds call: tensor([[ 2, 66, 58,  ...,  0,  0,  0]])
predicted index from cls: 0
this is self input ids before preds call: tensor([[ 2, 66, 58,  ...,  0,  0,  0]])
we found a double boys yeehaw
motif: GTTAAAA   count: 2
we found a double boys yeehaw
motif: GTTAAAA   count: 3
16
this is embeddings: Embedding(69, 768, padding_idx=0)
this is the indexes: None
this is the class name: None
3
2048
ref id length is: 2048
this is self input ids before preds call: tensor([[ 2, 46, 43,  ...,  0,  0,  0]])
this is input ids before ligattributionstensor([[ 2, 46, 43,  ...,  0,  0,  0]])
this is input ids shape before preds call: torch.Size([1, 2048])
this is position shape: torch.Size([1, 2048])
new pos ids = tensor([[  0,   1,   2,  ..., 509, 510, 511],
        [  0,   1,   2,  ..., 509, 510, 511],
        [  0,   1,   2,  ..., 509, 510, 511],
        [  0,   1,   2,  ..., 509, 510, 511]])
this is AM: tensor([1., 1., 1.,  ..., 0., 0., 0.])
this is input ids shape bef

this is input ids shape before preds call: torch.Size([4, 512])
this is position shape: torch.Size([4, 512])
this is AM: tensor([1., 1., 1.,  ..., 0., 0., 0.])
this is self input ids before preds call: tensor([[ 2, 58, 28,  ...,  0,  0,  0]])
predicted index from cls: 0
this is self input ids before preds call: tensor([[ 2, 58, 28,  ...,  0,  0,  0]])
we found a double boys yeehaw
motif: ATTTTAA   count: 2
we found a double boys yeehaw
motif: ATTTTAA   count: 3
we found a double boys yeehaw
motif: ATTTTAA   count: 4
we found a double boys yeehaw
motif: ATTTTAA   count: 5
we found a double boys yeehaw
motif: ATTTTAA   count: 6
we found a double boys yeehaw
motif: ATTTTAA   count: 7
we found a double boys yeehaw
motif: AAAAAAT   count: 2
21
this is embeddings: Embedding(69, 768, padding_idx=0)
this is the indexes: None
this is the class name: None
4
2048
ref id length is: 2048
this is self input ids before preds call: tensor([[ 2,  7, 14,  ..., 37,  6,  3]])
this is input ids before liga

this is input ids shape before preds call: torch.Size([4, 512])
this is position shape: torch.Size([4, 512])
this is AM: tensor([1., 1., 1.,  ..., 1., 1., 1.])
this is self input ids before preds call: tensor([[ 2, 28, 36,  ..., 33, 54,  3]])
predicted index from cls: 0
this is self input ids before preds call: tensor([[ 2, 28, 36,  ..., 33, 54,  3]])
25
this is embeddings: Embedding(69, 768, padding_idx=0)
this is the indexes: None
this is the class name: None
15
2048
ref id length is: 2048
this is self input ids before preds call: tensor([[ 2, 38,  9,  ...,  5,  6,  3]])
this is input ids before ligattributionstensor([[ 2, 38,  9,  ...,  5,  6,  3]])
this is input ids shape before preds call: torch.Size([1, 2048])
this is position shape: torch.Size([1, 2048])
new pos ids = tensor([[  0,   1,   2,  ..., 509, 510, 511],
        [  0,   1,   2,  ..., 509, 510, 511],
        [  0,   1,   2,  ..., 509, 510, 511],
        [  0,   1,   2,  ..., 509, 510, 511]])
this is AM: tensor([1., 1., 1

...

this is input ids shape before preds call: torch.Size([1, 2048])
this is position shape: torch.Size([1, 2048])
new pos ids = tensor([[  0,   1,   2,  ..., 509, 510, 511],
        [  0,   1,   2,  ..., 509, 510, 511],
        [  0,   1,   2,  ..., 509, 510, 511],
        [  0,   1,   2,  ..., 509, 510, 511]])
this is AM: tensor([1., 1., 1.,  ..., 1., 1., 1.])
this is input ids shape before preds call: torch.Size([50, 2048])
this is position shape: torch.Size([50, 2048])
new pos ids = tensor([[  0,   1,   2,  ..., 509, 510, 511],
        [  0,   1,   2,  ..., 509, 510, 511],
        [  0,   1,   2,  ..., 509, 510, 511],
        ...,
        [  0,   1,   2,  ..., 509, 510, 511],
        [  0,   1,   2,  ..., 509, 510, 511],
        [  0,   1,   2,  ..., 509, 510, 511]])
this is AM: tensor([1., 1., 1.,  ..., 1., 1., 1.])
(tensor([[ 2,  9, 22,  ..., 26, 26,  3]]), tensor([[   0,    1,    2,  ..., 2045, 2046, 2047]]))
(tensor([[2, 0, 0,  ..., 0, 0, 3]]), tensor([[0, 0, 0,  ..., 0, 0, 0]]))
0

this is input ids before ligattributionstensor([[ 2, 14, 43,  ..., 53,  8,  3]])
this is input ids shape before preds call: torch.Size([1, 2048])
this is position shape: torch.Size([1, 2048])
new pos ids = tensor([[  0,   1,   2,  ..., 509, 510, 511],
        [  0,   1,   2,  ..., 509, 510, 511],
        [  0,   1,   2,  ..., 509, 510, 511],
        [  0,   1,   2,  ..., 509, 510, 511]])
this is AM: tensor([1., 1., 1.,  ..., 1., 1., 1.])
this is input ids shape before preds call: torch.Size([1, 2048])
this is position shape: torch.Size([1, 2048])
new pos ids = tensor([[  0,   1,   2,  ..., 509, 510, 511],
        [  0,   1,   2,  ..., 509, 510, 511],
        [  0,   1,   2,  ..., 509, 510, 511],
        [  0,   1,   2,  ..., 509, 510, 511]])
this is AM: tensor([1., 1., 1.,  ..., 1., 1., 1.])
this is input ids shape before preds call: torch.Size([50, 2048])
this is position shape: torch.Size([50, 2048])
new pos ids = tensor([[  0,   1,   2,  ..., 509, 510, 511],
        [  0,   1,   2, 

we found a double boys yeehaw
motif: TTATAAT   count: 17
we found a double boys yeehaw
motif: TTATAAT   count: 18
we found a double boys yeehaw
motif: TTATAAT   count: 19
we found a double boys yeehaw
motif: TTATAATA   count: 21
we found a double boys yeehaw
motif: AAGAAGA   count: 27
we found a double boys yeehaw
motif: AAGAAGA   count: 28
we found a double boys yeehaw
motif: AAGAAGA   count: 29
we found a double boys yeehaw
motif: AAGAAGA   count: 30
we found a double boys yeehaw
motif: AAGAAGA   count: 31
we found a double boys yeehaw
motif: AAGAAGAG   count: 6
we found a double boys yeehaw
motif: AAGAAGAG   count: 7
we found a double boys yeehaw
motif: AAGAAGAG   count: 8
we found a double boys yeehaw
motif: AAGAAGAG   count: 9
we found a double boys yeehaw
motif: AAGAAGAG   count: 10
we found a double boys yeehaw
motif: AAGAAGAG   count: 11
we found a double boys yeehaw
motif: AAGAAGAG   count: 12
we found a double boys yeehaw
motif: AAGAAGAG   count: 13
we found a double boys yee

this is input ids shape before preds call: torch.Size([50, 2048])
this is position shape: torch.Size([50, 2048])
new pos ids = tensor([[  0,   1,   2,  ..., 509, 510, 511],
        [  0,   1,   2,  ..., 509, 510, 511],
        [  0,   1,   2,  ..., 509, 510, 511],
        ...,
        [  0,   1,   2,  ..., 509, 510, 511],
        [  0,   1,   2,  ..., 509, 510, 511],
        [  0,   1,   2,  ..., 509, 510, 511]])
this is AM: tensor([1., 1., 1.,  ..., 0., 0., 0.])
(tensor([[ 2, 36, 65,  ...,  0,  0,  0]]), tensor([[   0,    1,    2,  ..., 2045, 2046, 2047]]))
(tensor([[2, 0, 0,  ..., 0, 0, 0]]), tensor([[0, 0, 0,  ..., 0, 0, 0]]))
0
[tensor([[ 2, 36, 65,  ..., 21,  5,  3],
        [ 2,  5,  5,  ..., 10, 25,  3],
        [ 2, 23, 13,  ..., 67, 63,  3],
        [ 2, 46, 42,  ...,  0,  0,  0]]), tensor([[  0,   1,   2,  ..., 509, 510, 511],
        [  0,   1,   2,  ..., 509, 510, 511],
        [  0,   1,   2,  ..., 509, 510, 511],
        [  0,   1,   2,  ..., 509, 510, 511]])]
torch.Size(

we found a double boys yeehaw
motif: TCTCACA   count: 2
we found a double boys yeehaw
motif: TCTAAAAA   count: 2
we found a double boys yeehaw
motif: AGTTGGT   count: 3
we found a double boys yeehaw
motif: AGTTGGT   count: 4
we found a double boys yeehaw
motif: AGTTGGT   count: 5
we found a double boys yeehaw
motif: AGTTGGT   count: 6
we found a double boys yeehaw
motif: AGTTGGT   count: 7
we found a double boys yeehaw
motif: AGTTGGT   count: 8
we found a double boys yeehaw
motif: AGTTGGT   count: 9
we found a double boys yeehaw
motif: AGTTGGT   count: 10
we found a double boys yeehaw
motif: AGTTGGTG   count: 2
we found a double boys yeehaw
motif: TGTAAAAC   count: 2
we found a double boys yeehaw
motif: TGTAAAAC   count: 3
we found a double boys yeehaw
motif: TATATATT   count: 7
we found a double boys yeehaw
motif: AAAACCAA   count: 4
we found a double boys yeehaw
motif: AAAACCAATT   count: 2
we found a double boys yeehaw
motif: CTTCTCC   count: 6
we found a double boys yeehaw
motif: C

In [5]:
#iterate through the dictionary
final_motifs = {}
for x in m:
    att_val = m.get(x)
    count = m_count.get(x)
    val = float(att_val*count)
    print(x)
    print(val)
    final_motifs[x] = val
print(final_motifs)

AGGCTTTAAAA
0.1525307486066746
TCGATCCACT
0.06818991439796826
ACACATT
0.6216192359219919
TTATAAAAA
0.45793232447563426
AGGCCTCAT
0.0084791163059817
ATTTCTTTCTCTATATAATGACT
0.20713723421542302
AAATTCCGT
0.0682848462478414
GAAATTCGGCTG
0.13565074154072942
TCCGTCGTC
0.10261864493566122
GTGCGGCTGCTC
0.07767398126329922
GAAAATCGCAACGCT
0.11190487569789322
GTGACGAGT
0.05423502125803839
GATGGGA
7.186553107015046
TTTTAACTCA
0.06900134225183788
TCCGGCA
0.8877751130452447
GACGTCTCAACCGT
0.1525826502852125
CTCCTCCC
4.533856009062972
TTACAGATT
0.00803218845316831
GTTTTAG
1.7952109931472802
TTCCTCTACGGAATT
0.028931036591110532
GTCTAAA
0.005607255201946074
TTTTTTT
2800.008822833129
ATCTTGGA
0.018458726875604983
CAAGCGC
0.016940788237427923
GATTTAG
21.973891815561704
GTTTTCGATGCAAAAAA
0.03910125298327463
TATTTATCTTT
0.047695071482819054
ATTACGT
2.621950604447411
TCACTTTTTTTTTTTT
0.2299835517198819
AAATTAAAC
0.09839186527300413
ACATATTT
0.260287952596477
TAAAAAGA
2.557414781813864
TCTAAAA
13.717453466

ACCAGATGA
0.04090878451981722
TCGCCGA
0.04319404671438736
ACGAAAGAGAGAGA
0.10428164296160711
ACTTTACTT
0.023918391750401686
TTCCCCTACCCCA
0.11161660363384494
TAAACATGTCGCC
0.04492909585759164
GCCACAT
0.026723279016165412
TTAACCGACGACT
0.05384312295629336
TTTTGTTTT
9.56309473710404
TTCCATAATTTTGATTTAAATT
0.11439039871732813
TAAGCAAC
0.018287871604991682
GTTTTGGG
0.00718116256883188
TACACTA
0.07088573419246952
TATACAATA
0.050895041335309754
ATATACATA
0.19114499749506283
CCCCGTC
0.17750562896540126
GGAATTTT
0.025926073213473268
TGCCGAT
0.013074319150277047
CTAATTGGCTGTT
0.028127035621972194
TTAGCCACATCCA
0.033069058039067754
CAACGGACAAT
0.04686000655017012
GCCGCATTCCAAA
0.05182152152893507
TTTGATTCCATCAA
0.035304359391733486
GGAGCAAC
0.011405079258947662
CAGATGTTTCTT
0.01503648928024758
AATGAGCAAG
0.04872023465612677
TAACATC
2.1081464299469483
TCGCATACCC
0.023876708915177604
TCACTTT
23.046846015127215
ATTTATTTTTA
0.6969492231735605
ACTCCGGTTGGAATTAATTAAGC
0.10541704873821053
TGCGTCTTTAAT


TTAGAAAC
0.05784523765761329
TCTGTTA
0.02359196478031093
TGGTTTGTTT
0.23485524536051205
ATAAGAAA
0.03034056736616877
AAGCGAG
0.03478803554751919
GCGTTTT
0.022716060311440158
GCGGTCG
0.019677068646007195
CAACAAA
2.4835162321919246
CAGATTCATTCT
0.11836142355438711
ACGAGGTGGC
0.044018645433719104
ATGCCAT
2.8469382931970855
ACGCAAT
0.7392259916772606
TAAACAAGAA
0.0686153471166094
TAAACTT
1.6047755404970965
GCAGCAGAAAGT
0.2932579808492471
TACATAAACATAAATCAAT
0.41478031614839433
GGGTGGAAGGGATGTA
0.14485789544110123
AGCTGCCA
0.072385698882775
TTTACGT
1.0911955199437093
CTTTCAT
2.775734799457398
TATTTATT
5.268797069091864
TAAATCA
0.12362118678689965
AGAGAATC
0.029940483517079956
AGGGAAGATAA
0.08217173758594751
ACGGGGATGCGAGT
0.1863047713428646
ACGAGCTAGCCC
0.1305539561228664
CCTCGATATCGCACCT
0.17369749578398191
TCTGTAA
12.959930563593451
ATGTGAAA
3.1659918199741424
AGTTATGAAA
0.05076862431659166
AGTCGGG
0.06351011689233906
AGCGTCAG
0.09563787770478221
ATGTATTAATTTT
0.1826683689506703
GTAAGAGGA

TTCGGCCTC
0.18712900803320903
CGGATCGGATCCGGATCGGATCTCGGAT
0.4839941267731037
TCGAATCCGGAT
0.3033473979251846
TCTCGGA
0.06236578209807778
TTGTAGCTCAGTCCTT
0.1639099372702053
CACGGTTT
0.05414696549832692
TGTACAC
0.04601633711480708
AAATTGAGCGTACATGTG
0.17426973091657452
GGATACACGTG
0.06176114744668808
TTAACCTAAA
0.08728884307028124
CTAAAGG
3.6324580445648094
ATGAGAGA
0.7304619588175122
GACCATTGTT
0.2152578814304226
ATCCTGACTCA
0.09062812475840425
CAGTCGC
0.046266293649115914
TCCTGAAA
0.05136329443715823
ACAAAAA
2.2157911463462026
GGATTTAA
0.06551245284453523
CCGACTGAGCC
0.09218491101438717
ATTGTTTATTC
0.31142014595345413
TGTGTATT
0.12468108899499947
TGGGTGAAAA
0.12236353614425252
ACAGAGGA
0.19052873297225467
TGAACAGAGAC
0.2633647566881974
GCAACCATAGTC
0.22078574765015138
TGTCGCCGT
0.15889038065273878
TAGCTTGACATA
0.1188964411462384
AAGAAACAACATCCAT
0.05691265230672288
ATGAAGAAGAAAGA
0.03025220745671818
AACCCACTTGTT
0.040346953262266054
TTGCCAGGA
0.035039238724337
GTTTGTTT
0.832049610521

0.04530036642885809
CATTGCA
0.011300691371196003
ACTTCAATGGAACTCTTCTCAC
0.1422745351879881
TCCCTCG
0.24898261622350032
TTCACGCAT
0.041788782536483354
GCAGCTCGC
0.04110631841186642
CCGGAGA
0.07381598960731121
AGCGAAGACAG
0.0987857535088441
CAGGAGA
0.28392197418836673
CCACGAGCT
0.13814661908528747
CACTCTT
1.4016148910207062
TCATAATC
0.11768641461215577
CCCCTGAGCTTTGA
0.21715378000199018
ATTGAATCT
0.07189879383270495
CTGTTCAATA
0.19483804474735728
TCAGTTG
0.09335452829296387
ACTTTTT
17.388398016467725
GTAAAACGA
0.1541249760702526
GGGACACAGGAGAGAA
0.3018273186013609
TCATGACA
0.54671129546825
AGTAGAAAAA
0.35580344111075923
TGTTAAAA
43.085720253474186
TGCTTCA
0.10624721172332925
CTTTGTTTTAT
0.06337467308538618
TGTGATATC
0.040281485729286824
AGCTGCCCGCGG
0.03947330599375068
GTTTAAACGGG
0.046201718416281276
TGTATCCGT
0.032788077150264716
TTTATTTA
8.923973776360608
TTAACGGG
0.02810465770681928
TTTACCT
0.14870839101155842
TTTTAAGGCCCGTTTATAAACGGGCGCAG
0.13184890892036055
CCGATTTAAA
0.04677716618

...

0.17492706205541825
GTTTTGGGGAAAAGG
0.17950848219631743
AAAAAAATGAAA
0.05520186961321147
AGTCTTTGTT
0.13077121215790719
AATGCTTAAAT
0.1539069260713909
ATATACATTCA
0.18332537143328564
CCATCACTTTC
0.2853194679338682
CTTCATAA
0.10604336439372586
GCGCTCGTGAGA
0.07182244590646902
TAATCATG
0.03588224167418266
CATTAAGAT
0.03461131750209037
TAAGTGA
0.032946177690271417
TTATAATTCA
0.10366712296604112
CATTTAAATAT
0.09429290746846322
AGCTAAAA
0.05632515323642033
GATTAAATA
0.09269287746432378
ATTTATATTTTTGTATTTTATAGATGTAT
0.4780787265854715
AATACTGT
0.4180827438091256
TGTGTTCG
0.24986186011553563
AAAATAAG
0.32626453224677204
TTGTTTAAGTC
0.275841204069978
TATATTAATATA
0.15696092802901426
CATAATTTTTAAT
0.14084661203187102
CTCACCCT
0.0747389976152434
CAAGTCG
0.021610199365708096
TTTGTAAAAATGA
0.1570728506921434
TACTTATTTAAT
0.1960892523314056
TGAAAAGA
0.10164473707040447
GCATTTTGTTT
0.4412595227569664
CCCTTCGTTACA
0.5964489151155542
TAAGTGGTTTTTTT
0.5210950931679132
TCGGCAGTG
0.2564898874658913
GAGAA

0.06076890403072424
TTAATAAGA
0.1287959352366546
CTAACTTTACAAT
0.1946539466920678
TCACTTTTG
0.12282651910434114
TGGTATAATA
0.12992009375283772
TGATAATAATACA
0.16478115371723645
CTTTAAACCTT
0.23423572666623665
ATTTTTATATGGAAGT
0.11754184502379186
AGTTTTTTT
0.09913067521653744
TTTTTTAATG
0.26787667945754867
TCATTATAAG
0.08329553692454905
AGAAGAAAT
0.056404629736391564
AGAGCCCTCTG
0.0827714457406392
GTTGCCAAA
0.05213661865521208
TGAGCACTCTTC
0.1125467408099482
GAGGAGAG
0.014796984121141147
TAAGCAGGCCAAGGCT
0.10901249909664898
GGACTGA
0.006483753299138842
AGTTAATT
0.012490444586449831
CAAGAACTAAAA
0.033704235073620865
GACAGGTT
0.03083306356521973
TGGAATGCAG
0.04506735601119722
CATCATTT
0.09620472684980155
TCTAATAG
0.043565127346227556
AAGAACAAACATT
0.10130343735997693
AAATGTCTA
0.029638297656079858
ACCCTTTTCCA
0.056094991501738196
CTCTTGTT
0.1571792358448001
TGTGGTCG
0.056752101265733004
CTGAGAT
0.01248581503291261
ATGTATTTATTTTTTGTC
0.06925645648749579
TGGAAAAT
0.014755698236437343
TAATAA

CCGGCCAGTC
0.08527254037801657
TCGTCGTTTGC
0.09576311776991776
TTTTGCGGC
0.06282337256005341
TCACGCAAA
0.09394402175056815
CAAATTTTCCCAA
0.09990522678083719
CACTAGC
0.013716975680883833
ATTTTCCTTTTACGTTTA
0.138698255488048
TTTTACTCA
0.05778901663119307
CCTTTTAT
0.033311648369926304
TAATACT
0.2518722885009771
TCTAAACCTTGTT
0.16351654793971906
ACTAATTGG
0.18839009333372117
GTTTTGACC
0.17124896117689914
GCTACTT
0.07354666327015755
ATCACAATC
0.0691673156073209
CTTCGTTACGCTATTAT
0.2880370140028769
TGATGTA
0.16099267043790666
ATGCAGGCTCGGT
0.3843253423999881
TGGACTAAT
0.10454509366474746
ACAACATT
0.04169947011029783
TTACCGAA
0.10053387639628457
TGTCGGT
0.15165958703313803
TTGTGATATAGCTT
0.16310962417468317
AGCATTTA
0.030992008982198695
AATTAAATTACAA
0.05089691259673175
TTGGCTTATTTCA
0.12577460942370294
ATCGACTGGTTGAA
0.11530554722834316
TCATTTTAATTT
0.14713655156292244
TTTAAAATAACT
0.10555132862454467
TAAACAAGAG
0.057418016058477
AAAACGTA
0.20058001871117156
CACCTCA
0.13515829082331277
CTAGT

0.042156395805564385
ACCGTGCC
0.046117878168657186
AAAATTTTT
0.02551337501720515
TGTTTACATTG
0.08456223950003608
TATTATTTA
0.03506445628273394
TGTACTC
0.03323226763686588
TTTAAAATTG
0.08845601265835865
TGTTATGA
0.1783237222969645
GAAACTC
0.19952322554708682
TAATAACCAA
0.49847632532525926
AAGTTTAAAA
0.15686300425483135
GCATTACACA
0.16285110509834086
TAAAAGAAA
0.05355906139377502
AAAAAAATATGA
0.11022878583133258
AAATATTTT
0.04747285519817506
TCGATTAG
0.04200261802401117
CATGAGATGTATTTTT
0.08777951066771363
ATGTTACTT
0.017103814064688343
ATTAACAA
0.03423076591789629
CATTTTAGCACGATGCT
0.09980836149287405
ACCGCGTGCC
0.07131936884831483
AAAACACA
0.061713607427274435
AAAAAAAAAAGAA
0.1256745409255067
TCTTAAAACCTCAG
0.19653779984932387
CTTGCGCACGAA
0.28009562342168287
CCACGTAAC
0.12482704031518982
ACGTTGTT
0.06382129374576942
CACTTATATTACC
0.06764366560781047
AAATTTCAT
0.030683690651879106
GAACTTAAATGTGAT
0.04446435474608031
TATAATAA
0.18402806706360436
ATCTCATTTTAA
0.024202950064920008
AGTGTTA

TCATGTACATGT
0.1750553939417736
TTACTACACTGA
0.060516600282568535
TTAAATACT
0.0453393910281554
AGCCATGA
0.11172435800902257
GCTTAATTCACAAAGAGAGAGGGCATA
0.13380019785768155
AAATACTCACA
0.04134083117776895
CTCTCTAGCCAT
0.03799524592855555
GGGTTCTCTCTC
0.040105664177730004
TTAGTCAT
0.026921650159111233
TCCGCTCCTA
0.08137270923747782
TCTAGAAA
0.17943444680045184
AGGGTTTGA
0.20914573228725122
TAGATCTTCTGGATCTTGGTTT
0.4366562896120464
AATCTGT
0.054931028641976784
ATGGTTGAT
0.06515732129570895
ATTGTTGGTTTTGATT
0.17178956354414088
ATGTTGTTCAAGT
0.08945237644956236
TAGATGATG
0.06675355924324033
TGTGTGTTTTTGCTTTG
0.21620822492662664
TATCATA
0.03832653031030545
TTGATTAA
0.05081508927637213
TCTGTGTTT
0.062356791373650224
ACTTCATTAG
0.12801567267898326
TTCAGTTTCTG
0.18808403313236124
AGTCTGGTG
0.06792618229403576
GCTGAGATCCGTGAT
0.44863513140365086
GCTGAGGAAGCAGCAAGAGCTT
0.5780837652095354
TCCCAGAG
0.051153692219659166
CCCTGCT
0.028840192257861944
GCTAAGAAGC
0.12701755951777013
CAAACCAA
0.039636934

In [6]:
import json

json = json.dumps(final_motifs)
print(json)
f = open("Bo_motif_dict_idx.json","w")
f.write(json)
f.close()

In [7]:
import json
ff = open("Bo_motif_dict_idx.json")
final_motifs = json.load(ff)

from PIL import Image
import matplotlib.pyplot as plt
from wordcloud import WordCloud

wc = WordCloud(background_color="white",width=1000,height=1000, max_words=10,relative_scaling=0.5,normalize_plurals=False).generate_from_frequencies(final_motifs)
plt.imshow(wc)

In [1]:
#tests the json file opens
import json
ff = open("Bo_motif_dict_idx.json")
final_motifs = json.load(ff)


#prints highest value motifs 
import operator
sorted_m = sorted(final_motifs.items(), key=lambda kv: kv[1])
#sorted_m.reverse() = sorted(m.items(), key=operator.itemgetter(1))
sorted_m.reverse()
sorted_m

[('AAAAAAAAAA', 2842.211640328658),
 ('TTTTTTT', 2800.008822833129),
 ('AAAAAAAA', 2569.566111986621),
 ('AAAAAAA', 1965.4694288877338),
 ('TTTTTTTT', 1915.1529149255716),
 ('AAAAAAAAA', 1399.2718655964666),
 ('AAAAAAAAAAA', 890.7907576138388),
 ('TTTTTTTTT', 461.15676551242274),
 ('TTTTGTT', 275.1914848217984),
 ('TTATAAAT', 243.15939120132057),
 ('TTTTTATT', 225.61105396569377),
 ('TTATTTT', 213.26398954257783),
 ('ATTTTTA', 210.9687716350812),
 ('TATATATAT', 207.54126172976197),
 ('TGTGTGT', 198.1078282786304),
 ('ATTTTTTT', 158.8847896043121),
 ('ATTTTAA', 158.86521224912462),
 ('TTTTTTTA', 156.8831784240812),
 ('TTTTTTTTTTT', 153.10546866051354),
 ('ATTTTTT', 148.06223708130332),
 ('AATAAAT', 143.7770674662335),
 ('TTAAAAA', 142.36266899906317),
 ('AATTTAA', 125.8243370189466),
 ('TTTTAAT', 125.27235684480263),
 ('AACAGAA', 124.89290370785389),
 ('AAGAAGAG', 122.36519614788864),
 ('TTTTTTTTTT', 116.99227975483963),
 ('CATTAAA', 116.8346916349478),
 ('ACACAAA', 115.00944305585018),

In [2]:
top_50 = []
for x in sorted_m:
    top_50.append(x[0])
    if(len(top_50) == 50):
        break

In [3]:
with open("Bo_motif_top50.txt", "w") as txt_file:
    i = 0
    for line in top_50:
        if(i<49):
            txt_file.write(line + "\n")
            i = i + 1
        else:
            txt_file.write(line)

In [ ]:
### send this text file to the bash / R combination of significance
### copy back the motifs and sigs.txt

In [4]:
lines = []
sigs = open("motif_sigs.txt")
for line in sigs:
    line = line.strip()
    if(" " in line):
        line = line.split()
        line = float(line[1])
    lines.append(line)
print(lines)

['AAAAAAAAAA', 8.846178e-07, 'TTTTTTT', 3.444227e-11, 'AAAAAAAA', 4.103523e-10, 'AAAAAAA', 4.336063e-13, 'TTTTTTTT', 8.587945e-13, 'AAAAAAAAA', 2.51491e-09, 'AAAAAAAAAAA', 7.943025e-05, 'TTTTTTTTT', 2.242878e-08, 'TTTTGTT', 1.34523e-08, 'TTATAAAT', 0.2793013, 'TTTTTATT', 0.00377824, 'TTATTTT', 0.0002804987, 'ATTTTTA', 0.3766007, 'TATATATAT', 0.3562371, 'TGTGTGT', 0.001442316, 'ATTTTTTT', 0.0002235089, 'ATTTTAA', 0.8633181, 'TTTTTTTA', 0.0002533151, 'TTTTTTTTTTT', 6.919431e-06, 'ATTTTTT', 6.314392e-07, 'AATAAAT', 0.2048574, 'TTAAAAA', 0.0008390131, 'AATTTAA', 0.01942382, 'TTTTAAT', 0.04638087, 'AACAGAA', 4.104608e-10, 'AAGAAGAG', 6.514073e-06, 'TTTTTTTTTT', 1.9926e-06, 'CATTAAA', 0.8617555, 'ACACAAA', 9.819665e-05, 'TTTATTT', 2.389528e-06, 'ACACACA', 1.992472e-07, 'TTTTAAA', 0.05729805, 'AAAATAA', 0.009509219, 'GTTAATT', 0.2229813, 'TAAATAAA', 1.0, 'TTATTTA', 0.06493227, 'GAAAAAAA', 3.568824e-08, 'CCATTTT', 0.4699515, 'ACCAATT', 0.4390382, 'TTTTTTTTTTTT', 0.0002703155, 'GTTTTTG', 0.0181

In [5]:
top_50_sig_motifs = {}
i = 0
while i < len(lines):
    my_motif = lines[i]
    sig_value = lines[i+1]
    if(sig_value<0.05):
        top_50_sig_motifs[my_motif] = sig_value
    i = i + 2
print(len(top_50_sig_motifs))
print(top_50_sig_motifs)


35
{'AAAAAAAAAA': 8.846178e-07, 'TTTTTTT': 3.444227e-11, 'AAAAAAAA': 4.103523e-10, 'AAAAAAA': 4.336063e-13, 'TTTTTTTT': 8.587945e-13, 'AAAAAAAAA': 2.51491e-09, 'AAAAAAAAAAA': 7.943025e-05, 'TTTTTTTTT': 2.242878e-08, 'TTTTGTT': 1.34523e-08, 'TTTTTATT': 0.00377824, 'TTATTTT': 0.0002804987, 'TGTGTGT': 0.001442316, 'ATTTTTTT': 0.0002235089, 'TTTTTTTA': 0.0002533151, 'TTTTTTTTTTT': 6.919431e-06, 'ATTTTTT': 6.314392e-07, 'TTAAAAA': 0.0008390131, 'AATTTAA': 0.01942382, 'TTTTAAT': 0.04638087, 'AACAGAA': 4.104608e-10, 'AAGAAGAG': 6.514073e-06, 'TTTTTTTTTT': 1.9926e-06, 'ACACAAA': 9.819665e-05, 'TTTATTT': 2.389528e-06, 'ACACACA': 1.992472e-07, 'AAAATAA': 0.009509219, 'GAAAAAAA': 3.568824e-08, 'TTTTTTTTTTTT': 0.0002703155, 'GTTTTTG': 0.01818449, 'TTCTTCTT': 4.068548e-11, 'ATTTAAATTT': 0.009025018, 'AATAAAA': 0.0004141563, 'GAAAAAAAAA': 0.002500658, 'TTTAAAT': 0.03789915, 'TCTCTCT': 2.352159e-20}


In [6]:
#store top 50 motifs that are sig into new json file
import json

json = json.dumps(top_50_sig_motifs)
print(json)
f = open("Bo_sig_motifs_top50.json","w")
f.write(json)
f.close()

{"AAAAAAAAAA": 8.846178e-07, "TTTTTTT": 3.444227e-11, "AAAAAAAA": 4.103523e-10, "AAAAAAA": 4.336063e-13, "TTTTTTTT": 8.587945e-13, "AAAAAAAAA": 2.51491e-09, "AAAAAAAAAAA": 7.943025e-05, "TTTTTTTTT": 2.242878e-08, "TTTTGTT": 1.34523e-08, "TTTTTATT": 0.00377824, "TTATTTT": 0.0002804987, "TGTGTGT": 0.001442316, "ATTTTTTT": 0.0002235089, "TTTTTTTA": 0.0002533151, "TTTTTTTTTTT": 6.919431e-06, "ATTTTTT": 6.314392e-07, "TTAAAAA": 0.0008390131, "AATTTAA": 0.01942382, "TTTTAAT": 0.04638087, "AACAGAA": 4.104608e-10, "AAGAAGAG": 6.514073e-06, "TTTTTTTTTT": 1.9926e-06, "ACACAAA": 9.819665e-05, "TTTATTT": 2.389528e-06, "ACACACA": 1.992472e-07, "AAAATAA": 0.009509219, "GAAAAAAA": 3.568824e-08, "TTTTTTTTTTTT": 0.0002703155, "GTTTTTG": 0.01818449, "TTCTTCTT": 4.068548e-11, "ATTTAAATTT": 0.009025018, "AATAAAA": 0.0004141563, "GAAAAAAAAA": 0.002500658, "TTTAAAT": 0.03789915, "TCTCTCT": 2.352159e-20}


# Classifier Based off Presence of Sig Motifs

In [ ]:
#load motifs that were significant in top 50 attention score motifs
import json
ff = open("Bo_sig_motifs_top50.json")
sig_motifs_in_top50 = json.load(ff)
ff.close()

In [ ]:
#load sequences and equivalent label

import pandas as pd
df = pd.read_csv("holdout.csv")
print(df)
test_seqs = df["Sequence"]
test_labels=[]
for x in df["Target"]:
    if("not_lncRNA" in x):
        test_labels.append(1)
    else:
        test_labels.append(0)

In [ ]:
from sklearn.metrics import accuracy_score

accuracies = []

#loop through different thresholds to find best threshold of accuracy
for i in range(0,len(sig_motifs_in_top50)):
    #loop through each available sequences to test
    pred_labels = []
    for seq in test_seqs:
        #how many of the motifs are found in the seq
        sig_motif_count = 0
        for motif in sig_motifs_in_top50:
            if motif in seq:
                sig_motif_count = sig_motif_count + 1
        #check to see if the # of motifs found is above the current test threshold
        if(sig_motif_count >= i):
            pred_labels.append(0)
        else:
            pred_labels.append(1)
    accuracy = accuracy_score(test_labels, pred_labels)
    accuracies.append(accuracy)
    print("Accuracy for threshold "+str(i)+" is "+str(accuracy))

In [ ]:
from sklearn.metrics import confusion_matrix

pred_labels = []
for seq in test_seqs:
    #how many of the motifs are found in the seq
    sig_motif_count = 0
    for motif in sig_motifs_in_top50:
        if motif in seq:
            sig_motif_count = sig_motif_count + 1
    #check to see if the # of motifs found is above the current test threshold
    if(sig_motif_count >= 12):
        pred_labels.append(0)
    else:
        pred_labels.append(1)
accuracy = accuracy_score(test_labels, pred_labels)

cm = confusion_matrix(test_labels, pred_labels)
print(cm)